# Wine Review Analysis
1. Data Extraction  
2. Data Exploration & Preprocessing    
    2.1 Remove Null value  
    2.2 Lowercase text value   
    2.3 Country Feature Preprocessing  
    2.4 Grapes Variaty Feature Preprocessing
    
3. Features Extraction  
    3.1 Tokenizor  
    3.2 Stopwords Remover   
    3.3 TF-IDF Text Feature Extraction  
    3.4 Word2Vec Text Feature Extraction   
    3.5 Transform Points as categorical feature with Bucketizer  
    3.6 Transform Country, Taster_name, Variety as categorical features with StringIndexer and OneHotEncoderEstimator  
    3.7 Choose Top-K best features with ChiSqSelector    
    3.8 Create Feature Extraction Pipeline
    
4. Model Exploration  
    4.1 Classification  
    - 4.1.1 Features used
      - TF-IDF Features
      - Word2Vec Features
      - Numerical & Categorical Features
      - Combine Features
      - Selected Features  
      
   - 4.1.2 Models 
    - Logistic Regression
    - Support Vector Machine
    - Random Forest
    - MLPC (MultilayerPerceptronClassifier)
  
  4.2 Regression
  - Gradient Boosting Regression
  - Random Forest Regression
  - Linear Regression

5. Cross Validation & Hyper-Parameters Tuning  
    5.1 Classification Hyper-Parameters Tuning  
    5.2 Regression Hyper-Parameters Tuning

In [2]:
import pyspark
from pyspark.sql import SparkSession
spark = SparkSession.builder.getOrCreate() 

In [3]:
from pyspark.ml.feature import HashingTF, Tokenizer, IDF, StopWordsRemover, RegexTokenizer, Bucketizer, StringIndexer, OneHotEncoderEstimator, VectorAssembler, ChiSqSelector
from pyspark.sql import SparkSession
from pyspark.sql.functions import *
from pyspark.ml import Pipeline
from pyspark.ml.classification import LinearSVC, LogisticRegression, NaiveBayes, OneVsRest, MultilayerPerceptronClassifier, RandomForestClassifier
from pyspark.ml.evaluation import MulticlassClassificationEvaluator
from pyspark.sql import functions as F
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder
from pyspark.ml.feature import Word2Vec
from pyspark.ml.feature import NGram

## 1. Data Extraction

In [5]:
df = spark.sql('select * from wine1')

In [6]:
display(df)

id country description designation points price province region_1 region_2 taster_name taster_twitter_handle title variety winery 0 Italy Aromas include tropical fruit, broom, brimstone and dried herb. The palate isn't overly expressive, offering unripened apple, citrus and dried sage alongside brisk acidity. Vulkà Bianco 87 null Sicily & Sardinia Etna null Kerin O’Keefe @kerinokeefe Nicosia 2013 Vulkà Bianco (Etna) White Blend Nicosia 1 Portugal This is ripe and fruity, a wine that is smooth while still structured. Firm tannins are filled out with juicy red berry fruits and freshened with acidity. It's already drinkable, although it will certainly be better from 2016. Avidagos 87 15.0 Douro null null Roger Voss @vossroger Quinta dos Avidagos 2011 Avidagos Red (Douro) Portuguese Red Quinta dos Avidagos 2 US Tart and snappy, the flavors of lime flesh and rind dominate. Some green pineapple pokes through, with crisp acidity underscoring the flavors. The wine was all stainless-steel fermented. null 87 14.0 Oregon Willamette Valley Willamette Valley Paul Gregutt @paulgwine  Rainstorm 2013 Pinot Gris (Willamette Valley) Pinot Gris Rainstorm 3 US Pineapple rind, lemon pith and orange blossom start off the aromas. The palate is a bit more opulent, with notes of honey-drizzled guava and mango giving way to a slightly astringent, semidry finish. Reserve Late Harvest 87 13.0 Michigan Lake Michigan Shore null Alexander Peartree null St. Julian 2013 Reserve Late Harvest Riesling (Lake Michigan Shore) Riesling St. Julian 4 US Much like the regular bottling from 2012, this comes across as rather rough and tannic, with rustic, earthy, herbal characteristics. Nonetheless, if you think of it as a pleasantly unfussy country wine, it's a good companion to a hearty winter stew. Vintner's Reserve Wild Child Block 87 65.0 Oregon Willamette Valley Willamette Valley Paul Gregutt @paulgwine  Sweet Cheeks 2012 Vintner's Reserve Wild Child Block Pinot Noir (Willamette Valley) Pinot Noir Sweet Cheeks 5 Spain Blackberry and raspberry aromas show a typical Navarran whiff of green herbs and, in this case, horseradish. In the mouth, this is fairly full bodied, with tomatoey acidity. Spicy, herbal flavors complement dark plum fruit, while the finish is fresh but grabby. Ars In Vitro 87 15.0 Northern Spain Navarra null Michael Schachner @wineschach Tandem 2011 Ars In Vitro Tempranillo-Merlot (Navarra) Tempranillo-Merlot Tandem 6 Italy Here's a bright, informal red that opens with aromas of candied berry, white pepper and savory herb that carry over to the palate. It's balanced with fresh acidity and soft tannins. Belsito 87 16.0 Sicily & Sardinia Vittoria null Kerin O’Keefe @kerinokeefe Terre di Giurfo 2013 Belsito Frappato (Vittoria) Frappato Terre di Giurfo 7 France This dry and restrained wine offers spice in profusion. Balanced with acidity and a firm texture, it's very much for food. null 87 24.0 Alsace Alsace null Roger Voss @vossroger Trimbach 2012 Gewurztraminer (Alsace) Gewürztraminer Trimbach 8 Germany Savory dried thyme notes accent sunnier flavors of preserved peach in this brisk, off-dry wine. It's fruity and fresh, with an elegant, sprightly footprint. Shine 87 12.0 Rheinhessen null null Anna Lee C. Iijima null Heinz Eifel 2013 Shine Gewürztraminer (Rheinhessen) Gewürztraminer Heinz Eifel 9 France This has great depth of flavor with its fresh apple and pear fruits and touch of spice. It's off dry while balanced with acidity and a crisp texture. Drink now. Les Natures 87 27.0 Alsace Alsace null Roger Voss @vossroger Jean-Baptiste Adam 2012 Les Natures Pinot Gris (Alsace) Pinot Gris Jean-Baptiste Adam 10 US Soft, supple plum envelopes an oaky structure in this Cabernet, supported by 15% Merlot. Coffee and chocolate complete the picture, finishing strong at the end, resulting in a value-priced wine of attractive flavor and immediate accessibility. Mountain Cuvée 87 19.0 California Napa Valley Napa Virginie Boone @vboone Kirkland Signature 2011 Mount

## 2. Data Preprocessing

In [8]:
df_clean_null = df.dropna(subset=('description','price', 'points', 'country')).select('*')
df_clean_null = df_clean_null.selectExpr("id","description as description",'price as price','points as points','country as country','taster_name as taster_name', 'variety as variety')

In [9]:
print(df.count(), df_clean_null.count())

129971 120916

In [10]:
display(df_clean_null)

id description price points country taster_name variety 1 This is ripe and fruity, a wine that is smooth while still structured. Firm tannins are filled out with juicy red berry fruits and freshened with acidity. It's already drinkable, although it will certainly be better from 2016. 15.0 87 Portugal Roger Voss Portuguese Red 2 Tart and snappy, the flavors of lime flesh and rind dominate. Some green pineapple pokes through, with crisp acidity underscoring the flavors. The wine was all stainless-steel fermented. 14.0 87 US Paul Gregutt Pinot Gris 3 Pineapple rind, lemon pith and orange blossom start off the aromas. The palate is a bit more opulent, with notes of honey-drizzled guava and mango giving way to a slightly astringent, semidry finish. 13.0 87 US Alexander Peartree Riesling 4 Much like the regular bottling from 2012, this comes across as rather rough and tannic, with rustic, earthy, herbal characteristics. Nonetheless, if you think of it as a pleasantly unfussy country wine, it's a good companion to a hearty winter stew. 65.0 87 US Paul Gregutt Pinot Noir 5 Blackberry and raspberry aromas show a typical Navarran whiff of green herbs and, in this case, horseradish. In the mouth, this is fairly full bodied, with tomatoey acidity. Spicy, herbal flavors complement dark plum fruit, while the finish is fresh but grabby. 15.0 87 Spain Michael Schachner Tempranillo-Merlot 6 Here's a bright, informal red that opens with aromas of candied berry, white pepper and savory herb that carry over to the palate. It's balanced with fresh acidity and soft tannins. 16.0 87 Italy Kerin O’Keefe Frappato 7 This dry and restrained wine offers spice in profusion. Balanced with acidity and a firm texture, it's very much for food. 24.0 87 France Roger Voss Gewürztraminer 8 Savory dried thyme notes accent sunnier flavors of preserved peach in this brisk, off-dry wine. It's fruity and fresh, with an elegant, sprightly footprint. 12.0 87 Germany Anna Lee C. Iijima Gewürztraminer 9 This has great depth of flavor with its fresh apple and pear fruits and touch of spice. It's off dry while balanced with acidity and a crisp texture. Drink now. 27.0 87 France Roger Voss Pinot Gris 10 Soft, supple plum envelopes an oaky structure in this Cabernet, supported by 15% Merlot. Coffee and chocolate complete the picture, finishing strong at the end, resulting in a value-priced wine of attractive flavor and immediate accessibility. 19.0 87 US Virginie Boone Cabernet Sauvignon 11 This is a dry wine, very spicy, with a tight, taut texture and strongly mineral character layered with citrus as well as pepper. It's a food wine with its almost crisp aftertaste. 30.0 87 France Roger Voss Gewürztraminer 12 Slightly reduced, this wine offers a chalky, tannic backbone to an otherwise juicy explosion of rich black cherry, the whole accented throughout by firm oak and cigar box. 34.0 87 US Virginie Boone Cabernet Sauvignon 14 Building on 150 years and six generations of winemaking tradition, the winery trends toward a leaner style, with the classic California buttercream aroma cut by tart green apple. In this good everyday sipping wine, flavors that range from pear to barely ripe pineapple prove approachable but not distinctive. 12.0 87 US Matt Kettmann Chardonnay 15 Zesty orange peels and apple notes abound in this sprightly, mineral-toned Riesling. Off dry on the palate, yet racy and lean, it's a refreshing, easy quaffer with wide appeal. 24.0 87 Germany Anna Lee C. Iijima Riesling 16 Baked plum, molasses, balsamic vinegar and cheesy oak aromas feed into a palate that's braced by a bolt of acidity. A compact set of saucy red-berry and plum flavors features tobacco and peppery accents, while the finish is mildly green in flavor, with respectable weight and balance. 30.0 87 Argentina Michael Schachner Malbec 17 Raw black-cherry aromas are direct and simple but good. This has a juicy feel that thickens over time, with oak character and extract becoming more apparent. A flavor 

In [11]:
df_lower = df_clean_null.select('id','price', 'points', 'country', 'taster_name', 'variety', lower(df_clean_null['description']).alias('description'))
display(df_lower)

id price points country taster_name variety description 1 15.0 87 Portugal Roger Voss Portuguese Red this is ripe and fruity, a wine that is smooth while still structured. firm tannins are filled out with juicy red berry fruits and freshened with acidity. it's already drinkable, although it will certainly be better from 2016. 2 14.0 87 US Paul Gregutt Pinot Gris tart and snappy, the flavors of lime flesh and rind dominate. some green pineapple pokes through, with crisp acidity underscoring the flavors. the wine was all stainless-steel fermented. 3 13.0 87 US Alexander Peartree Riesling pineapple rind, lemon pith and orange blossom start off the aromas. the palate is a bit more opulent, with notes of honey-drizzled guava and mango giving way to a slightly astringent, semidry finish. 4 65.0 87 US Paul Gregutt Pinot Noir much like the regular bottling from 2012, this comes across as rather rough and tannic, with rustic, earthy, herbal characteristics. nonetheless, if you think of it as a pleasantly unfussy country wine, it's a good companion to a hearty winter stew. 5 15.0 87 Spain Michael Schachner Tempranillo-Merlot blackberry and raspberry aromas show a typical navarran whiff of green herbs and, in this case, horseradish. in the mouth, this is fairly full bodied, with tomatoey acidity. spicy, herbal flavors complement dark plum fruit, while the finish is fresh but grabby. 6 16.0 87 Italy Kerin O’Keefe Frappato here's a bright, informal red that opens with aromas of candied berry, white pepper and savory herb that carry over to the palate. it's balanced with fresh acidity and soft tannins. 7 24.0 87 France Roger Voss Gewürztraminer this dry and restrained wine offers spice in profusion. balanced with acidity and a firm texture, it's very much for food. 8 12.0 87 Germany Anna Lee C. Iijima Gewürztraminer savory dried thyme notes accent sunnier flavors of preserved peach in this brisk, off-dry wine. it's fruity and fresh, with an elegant, sprightly footprint. 9 27.0 87 France Roger Voss Pinot Gris this has great depth of flavor with its fresh apple and pear fruits and touch of spice. it's off dry while balanced with acidity and a crisp texture. drink now. 10 19.0 87 US Virginie Boone Cabernet Sauvignon soft, supple plum envelopes an oaky structure in this cabernet, supported by 15% merlot. coffee and chocolate complete the picture, finishing strong at the end, resulting in a value-priced wine of attractive flavor and immediate accessibility. 11 30.0 87 France Roger Voss Gewürztraminer this is a dry wine, very spicy, with a tight, taut texture and strongly mineral character layered with citrus as well as pepper. it's a food wine with its almost crisp aftertaste. 12 34.0 87 US Virginie Boone Cabernet Sauvignon slightly reduced, this wine offers a chalky, tannic backbone to an otherwise juicy explosion of rich black cherry, the whole accented throughout by firm oak and cigar box. 14 12.0 87 US Matt Kettmann Chardonnay building on 150 years and six generations of winemaking tradition, the winery trends toward a leaner style, with the classic california buttercream aroma cut by tart green apple. in this good everyday sipping wine, flavors that range from pear to barely ripe pineapple prove approachable but not distinctive. 15 24.0 87 Germany Anna Lee C. Iijima Riesling zesty orange peels and apple notes abound in this sprightly, mineral-toned riesling. off dry on the palate, yet racy and lean, it's a refreshing, easy quaffer with wide appeal. 16 30.0 87 Argentina Michael Schachner Malbec baked plum, molasses, balsamic vinegar and cheesy oak aromas feed into a palate that's braced by a bolt of acidity. a compact set of saucy red-berry and plum flavors features tobacco and peppery accents, while the finish is mildly green in flavor, with respectable weight and balance. 17 13.0 87 Argentina Michael Schachner Malbec raw black-cherry aromas are direct and simple but good. this has a juicy feel that thickens over time, with oak character an

In [12]:
display(df_lower.groupBy("country").avg("points").orderBy(F.desc("avg(points)")).take(20))

country avg(points) England 91.55072463768116 India 90.22222222222223 Austria 90.19078242229368 Germany 89.83632075471698 Canada 89.37795275590551 Hungary 89.1655172413793 China 89.0 France 88.73486723672367 Luxembourg 88.66666666666667 Italy 88.61818611800875 Australia 88.59546643417612 Switzerland 88.57142857142857 Morocco 88.57142857142857 US 88.56638717405326 Israel 88.49693251533742 Portugal 88.31671794871795 New Zealand 88.30841799709724 Turkey 88.08888888888889 Slovenia 88.0125 Bulgaria 87.93617021276596

In [13]:
df_lower = df_lower.withColumn('country_format',
                                                  F.when(F.col('country') == 'Argentina', 'ARG')\
                                                  .when(F.col('country') == 'Armenia', 'ARM')\
                                                  .when(F.col('country') == 'Australia', 'AUS')\
                                                  .when(F.col('country') == 'Austria', 'AUT')\
                                                  .when(F.col('country') == 'Bosnia and Herzegovina', 'BIH')\
                                                  .when(F.col('country') == 'Brazil', 'BRA')\
                                                  .when(F.col('country') == 'Bulgaria', 'BGR')\
                                                  .when(F.col('country') == 'Canada', 'CAN')\
                                                  .when(F.col('country') == 'Chile', 'CHL')\
                                                  .when(F.col('country') == 'China', 'CHN')\
                                                  .when(F.col('country') == 'Croatia', 'HRV')\
                                                  .when(F.col('country') == 'Cyprus', 'CYP')\
                                                  .when(F.col('country') == 'Czech Republic', 'CZE')\
                                                  .when(F.col('country') == 'Egypt', 'EGY')\
                                                  .when(F.col('country') == 'England', 'GBR')\
                                                  .when(F.col('country') == 'France', 'FRA')\
                                                  .when(F.col('country') == 'Georgia', 'GEO')\
                                                  .when(F.col('country') == 'Germany', 'DEU')\
                                                  .when(F.col('country') == 'Greece', 'GRC')\
                                                  .when(F.col('country') == 'Hungary', 'HUN')\
                                                  .when(F.col('country') == 'India', 'IND')\
                                                  .when(F.col('country') == 'Israel', 'ISR')\
                                                  .when(F.col('country') == 'Italy', 'ITA')\
                                                  .when(F.col('country') == 'Lebanon', 'LBN')\
                                                  .when(F.col('country') == 'Luxembourg', 'LUX')\
                                                  .when(F.col('country') == 'Macedonia', 'MKD')\
                                                  .when(F.col('country') == 'Mexico', 'MEX')\
                                                  .when(F.col('country') == 'Moldova', 'MDA')\
                                                  .when(F.col('country') == 'Morocco', 'MAR')\
                                                  .when(F.col('country') == 'New Zealand', 'NZL')\
                                                  .when(F.col('country') == 'Peru', 'PER')\
                                                  .when(F.col('country') == 'Portugal', 'PRT')\
                                                  .when(F.col('country') == 'Romania', 'ROU')\
                                                  .when(F.col('country') == 'Serbia', 'SRB')\
                                                  .when(F.col('country') == 'Slovakia', 'SVK')\
                                                  .when(F.col('country') == 'Slovenia', 'SVN')\
                                                  .when(F.col('country') == 'South Africa', 'ZAF')\
                                                  .when(F.col('country') == 'Spain', 'ESP')\
                                                  .when(F.col('country') == 'Switzerland', 'CHE')\
                                                  .when(F.col('country') == 'Turkey', 'TUR')\
                                                  .when(F.col('country') == 'US', 'USA')\
                                                  .when(F.col('country') == 'Ukraine', 'UKR')\
                                                  .when(F.col('country') == 'Uruguay', 'URY')\
                                                  .otherwise('') 
                                                  )


In [14]:
display(df_lower.groupBy("country_format").count())

country_format count BRA 47 ARM 2 FRA 17776 URY 109 ITA 16914 UKR 14 HRV 71 GBR 69 AUS 2294 MEX 70 SVK 1 HUN 145 NZL 1378 BIH 2 PER 16 LUX 6 TUR 90 AUT 2799 USA 54265 MAR 28 GEO 84 ZAF 1293 ISR 489 PRT 4875 CYP 11 CHL 4416 CAN 254 ROU 120 ARG 3756 ESP 6573 LBN 35 SVN 80 GRC 461 IND 9 MKD 12 CHN 1 DEU 2120 MDA 59 BGR 141 SRB 12 CHE 7 CZE 12

In [15]:
display(df_lower.groupBy("country_format").avg("points"))

country_format avg(points) BRA 84.65957446808511 ARM 87.5 FRA 88.73486723672367 URY 86.75229357798165 ITA 88.61818611800875 UKR 84.07142857142857 HRV 87.35211267605634 GBR 91.55072463768116 AUS 88.59546643417612 MEX 85.25714285714285 SVK 87.0 HUN 89.1655172413793 NZL 88.30841799709724 BIH 86.5 PER 83.5625 LUX 88.66666666666667 TUR 88.08888888888889 AUT 90.19078242229368 USA 88.56638717405326 MAR 88.57142857142857 GEO 87.67857142857143 ZAF 87.83139984532096 ISR 88.49693251533742 PRT 88.31671794871795 CYP 87.18181818181819 CHL 86.49547101449275 CAN 89.37795275590551 ROU 86.4 ARG 86.71033013844516 ESP 87.29073482428115 LBN 87.68571428571428 SVN 88.0125 GRC 87.2885032537961 IND 90.22222222222223 MKD 86.83333333333333 CHN 89.0 DEU 89.83632075471698 MDA 87.20338983050847 BGR 87.93617021276596 SRB 87.5 CHE 88.57142857142857 CZE 87.25

In [16]:
display(df_lower.groupBy("variety").count().orderBy('count', ascending = False))

variety count Pinot Noir 12785 Chardonnay 11077 Cabernet Sauvignon 9384 Red Blend 8466 Bordeaux-style Red Blend 5340 Riesling 4971 Sauvignon Blanc 4780 Syrah 4086 Rosé 3261 Merlot 3061 Zinfandel 2708 Malbec 2593 Sangiovese 2377 Nebbiolo 2331 Portuguese Red 2196 White Blend 2167 Sparkling Blend 2027 Tempranillo 1788 Rhône-style Red Blend 1404 Pinot Gris 1388 Cabernet Franc 1304 Champagne Blend 1211 Grüner Veltliner 1145 Pinot Grigio 1002 Portuguese White 986 Viognier 985 Gewürztraminer 955 Gamay 836 Shiraz 821 Petite Sirah 768 Bordeaux-style White Blend 695 Grenache 648 Barbera 617 Glera 604 Sangiovese Grosso 589 Tempranillo Blend 583 Carmenère 567 Chenin Blanc 533 Port 499 Corvina, Rondinella, Molinara 496 Albariño 474 Rhône-style White Blend 418 Pinot Blanc 386 Moscato 330 Nero d'Avola 326 Garnacha 325 Sauvignon 302 Aglianico 294 Verdejo 291 Petit Verdot 265 Meritage 259 Torrontés 247 Melon 241 Mourvèdre 226 Garganega 218 Vermentino 207 Blaufränkisch 206 Primitivo 203 Montepulciano 201 Prosecco 201 Zweigelt 182 G-S-M 180 Mencía 173 Touriga Nacional 173 Dolcetto 168 Roussanne 167 Tannat 167 Tinta de Toro 165 Verdicchio 161 Pinot Nero 159 Monastrell 146 Turbiana 146 Pinot Bianco 144 Pinotage 132 Sémillon 131 Fiano 130 Grenache Blanc 128 Vernaccia 126 Muscat 126 Alvarinho 116 Cabernet Sauvignon-Merlot 116 Friulano 112 Greco 111 Nerello Mascalese 111 Grillo 109 Bonarda 105 Viura 105 Cabernet Sauvignon-Syrah 102 Sherry 100 Tinto Fino 100 Sagrantino 93 Rosato 86 Malbec-Merlot 86 Ribolla Gialla 83 Arneis 80 Cabernet Blend 80 Lagrein 78 Godello 77 Carignan 77 St. Laurent 75 Rosado 75 Falanghina 75 Negroamaro 74 Spätburgunder 70 Fumé Blanc 70 Sauvignon Blanc-Semillon 68 Cortese 66 Arinto 66 Marsanne 65 Agiorgitiko 63 Austrian white blend 61 Provence red blend 59 Malbec-Cabernet Sauvignon 58 Syrah-Grenache 57 Verdelho 55 Vidal Blanc 55 Austrian Red Blend 54 Moscatel 54 Tempranillo-Cabernet Sauvignon 53 Furmint 52 Semillon-Sauvignon Blanc 52 Portuguese Sparkling 50 Grenache-Syrah 50 Petit Manseng 50 Alsace white blend 49 Alicante Bouschet 48 Müller-Thurgau 46 Pecorino 46 Sylvaner 46 Pinot Meunier 44 Assyrtico 43 Trebbiano 43 Graciano 42 Gros and Petit Manseng 42 Pedro Ximénez 42 Lambrusco 42 Malvasia 41 Cinsault 40 Cabernet Sauvignon-Carmenère 40 Weissburgunder 39 Garnacha Blanca 38 Shiraz-Viognier 38 Syrah-Cabernet Sauvignon 37 Saperavi 37 Carricante 37 Silvaner 37 Shiraz-Cabernet Sauvignon 36 Muscat Canelli 36 Frappato 36 Moschofilero 36 Lemberger 36 Traminer 34 Provence white blend 34 Encruzado 34 Merlot-Cabernet Sauvignon 33 Claret 33 Chardonnay-Viognier 33 Teroldego 32 Xinomavro 32 Rkatsiteli 32 Prugnolo Gentile 32 Tempranillo-Garnacha 32 Castelão 32 Petite Verdot 30 Aligoté 29 Carignane 29 Cannonau 28 Zibibbo 28 Fernão Pires 28 Chenin Blanc-Chardonnay 27 Dornfelder 27 Baga 27 Inzolia 27 Insolia 26 Kerner 26 Charbono 26 Touriga Nacional-Cabernet Sauvignon 26 Tannat-Cabernet 26 Catarratto 25 Loureiro 24 Trincadeira 24 Cabernet Sauvignon-Shiraz 24 Welschriesling 24 Jacquère 23 Colombard 23 Tokaji 23 Bobal 23 Schiava 23 Scheurebe 23 Auxerrois 23 Macabeo 23 Marsanne-Roussanne 22 Gamay Noir 22 Verdejo-Viura 22 Gros Manseng 22 Picolit 22 Merlot-Cabernet Franc 22 Gelber Muskateller 21 Monastrell-Syrah 21 Muskat Ottonel 21 Cabernet Sauvignon-Cabernet Franc 21 Xarel-lo 21 Rotgipfler 20 Passerina 20 Syrah-Mourvèdre 20 Orange Muscat 20 Corvina 20 Tocai Friulano 20 Cabernet Merlot 19 Malbec-Syrah 19 Albana 19 Nero di Troia 18 Syrah-Viognier 18 Cabernet Franc-Merlot 18 Palomino 18 Chambourcin 18 Tinto del Pais 18 Cabernet Sauvignon-Malbec 18 Picpoul 17 Antão Vaz 17 Lambrusco di Sorbara 17 Grenache-Carignan 17 Assyrtiko 17 Pinot Noir-Gamay 17 Plavac Mali 17 Hondarrabi Zuri 17 Lambrusco Grasparossa 16 Negrette 16 Malbec-Tannat 16 Norton 16 Malvasia Bianca 16 Baco Noir 16 Seyval Blanc 16 Syrah-Petite Sirah 16 Alfrocheiro 16 Tannat-Cabernet Franc 16 Prieto Picudo 15 Cabernet Franc-Cabernet Sauvignon 15 Syrah-Cabernet 15 Colombard-Sauvignon Blanc 15

## 3. Features Extraction

In [18]:
# regular expression tokenizer, remove punctuations 
regexTokenizer = RegexTokenizer(inputCol="description", outputCol="words", pattern="\\W")
wordsData = regexTokenizer.transform(df_lower)
display(regexTokenizer.transform(df_lower))

id price points country taster_name variety description words 1 15.0 87 Portugal Roger Voss Portuguese Red this is ripe and fruity, a wine that is smooth while still structured. firm tannins are filled out with juicy red berry fruits and freshened with acidity. it's already drinkable, although it will certainly be better from 2016. List(this, is, ripe, and, fruity, a, wine, that, is, smooth, while, still, structured, firm, tannins, are, filled, out, with, juicy, red, berry, fruits, and, freshened, with, acidity, it, s, already, drinkable, although, it, will, certainly, be, better, from, 2016) 2 14.0 87 US Paul Gregutt Pinot Gris tart and snappy, the flavors of lime flesh and rind dominate. some green pineapple pokes through, with crisp acidity underscoring the flavors. the wine was all stainless-steel fermented. List(tart, and, snappy, the, flavors, of, lime, flesh, and, rind, dominate, some, green, pineapple, pokes, through, with, crisp, acidity, underscoring, the, flavors, the, wine, was, all, stainless, steel, fermented) 3 13.0 87 US Alexander Peartree Riesling pineapple rind, lemon pith and orange blossom start off the aromas. the palate is a bit more opulent, with notes of honey-drizzled guava and mango giving way to a slightly astringent, semidry finish. List(pineapple, rind, lemon, pith, and, orange, blossom, start, off, the, aromas, the, palate, is, a, bit, more, opulent, with, notes, of, honey, drizzled, guava, and, mango, giving, way, to, a, slightly, astringent, semidry, finish) 4 65.0 87 US Paul Gregutt Pinot Noir much like the regular bottling from 2012, this comes across as rather rough and tannic, with rustic, earthy, herbal characteristics. nonetheless, if you think of it as a pleasantly unfussy country wine, it's a good companion to a hearty winter stew. List(much, like, the, regular, bottling, from, 2012, this, comes, across, as, rather, rough, and, tannic, with, rustic, earthy, herbal, characteristics, nonetheless, if, you, think, of, it, as, a, pleasantly, unfussy, country, wine, it, s, a, good, companion, to, a, hearty, winter, stew) 5 15.0 87 Spain Michael Schachner Tempranillo-Merlot blackberry and raspberry aromas show a typical navarran whiff of green herbs and, in this case, horseradish. in the mouth, this is fairly full bodied, with tomatoey acidity. spicy, herbal flavors complement dark plum fruit, while the finish is fresh but grabby. List(blackberry, and, raspberry, aromas, show, a, typical, navarran, whiff, of, green, herbs, and, in, this, case, horseradish, in, the, mouth, this, is, fairly, full, bodied, with, tomatoey, acidity, spicy, herbal, flavors, complement, dark, plum, fruit, while, the, finish, is, fresh, but, grabby) 6 16.0 87 Italy Kerin O’Keefe Frappato here's a bright, informal red that opens with aromas of candied berry, white pepper and savory herb that carry over to the palate. it's balanced with fresh acidity and soft tannins. List(here, s, a, bright, informal, red, that, opens, with, aromas, of, candied, berry, white, pepper, and, savory, herb, that, carry, over, to, the, palate, it, s, balanced, with, fresh, acidity, and, soft, tannins) 7 24.0 87 France Roger Voss Gewürztraminer this dry and restrained wine offers spice in profusion. balanced with acidity and a firm texture, it's very much for food. List(this, dry, and, restrained, wine, offers, spice, in, profusion, balanced, with, acidity, and, a, firm, texture, it, s, very, much, for, food) 8 12.0 87 Germany Anna Lee C. Iijima Gewürztraminer savory dried thyme notes accent sunnier flavors of preserved peach in this brisk, off-dry wine. it's fruity and fresh, with an elegant, sprightly footprint. List(savory, dried, thyme, notes, accent, sunnier, flavors, of, preserved, peach, in, this, brisk, off, dry, wine, it, s, fruity, and, fresh, with, an, elegant, sprightly, footprint) 9 27.0 87 France Roger Voss Pinot Gris this has great depth of flavor with its fresh apple and pear fruits and touch of spice. it's off dry while balanc

In [19]:
stopwordsRemover = StopWordsRemover(inputCol="words", outputCol="filtered")
display(stopwordsRemover.transform(wordsData))

id price points country taster_name variety description words filtered 1 15.0 87 Portugal Roger Voss Portuguese Red this is ripe and fruity, a wine that is smooth while still structured. firm tannins are filled out with juicy red berry fruits and freshened with acidity. it's already drinkable, although it will certainly be better from 2016. List(this, is, ripe, and, fruity, a, wine, that, is, smooth, while, still, structured, firm, tannins, are, filled, out, with, juicy, red, berry, fruits, and, freshened, with, acidity, it, s, already, drinkable, although, it, will, certainly, be, better, from, 2016) List(ripe, fruity, wine, smooth, still, structured, firm, tannins, filled, juicy, red, berry, fruits, freshened, acidity, already, drinkable, although, certainly, better, 2016) 2 14.0 87 US Paul Gregutt Pinot Gris tart and snappy, the flavors of lime flesh and rind dominate. some green pineapple pokes through, with crisp acidity underscoring the flavors. the wine was all stainless-steel fermented. List(tart, and, snappy, the, flavors, of, lime, flesh, and, rind, dominate, some, green, pineapple, pokes, through, with, crisp, acidity, underscoring, the, flavors, the, wine, was, all, stainless, steel, fermented) List(tart, snappy, flavors, lime, flesh, rind, dominate, green, pineapple, pokes, crisp, acidity, underscoring, flavors, wine, stainless, steel, fermented) 3 13.0 87 US Alexander Peartree Riesling pineapple rind, lemon pith and orange blossom start off the aromas. the palate is a bit more opulent, with notes of honey-drizzled guava and mango giving way to a slightly astringent, semidry finish. List(pineapple, rind, lemon, pith, and, orange, blossom, start, off, the, aromas, the, palate, is, a, bit, more, opulent, with, notes, of, honey, drizzled, guava, and, mango, giving, way, to, a, slightly, astringent, semidry, finish) List(pineapple, rind, lemon, pith, orange, blossom, start, aromas, palate, bit, opulent, notes, honey, drizzled, guava, mango, giving, way, slightly, astringent, semidry, finish) 4 65.0 87 US Paul Gregutt Pinot Noir much like the regular bottling from 2012, this comes across as rather rough and tannic, with rustic, earthy, herbal characteristics. nonetheless, if you think of it as a pleasantly unfussy country wine, it's a good companion to a hearty winter stew. List(much, like, the, regular, bottling, from, 2012, this, comes, across, as, rather, rough, and, tannic, with, rustic, earthy, herbal, characteristics, nonetheless, if, you, think, of, it, as, a, pleasantly, unfussy, country, wine, it, s, a, good, companion, to, a, hearty, winter, stew) List(much, like, regular, bottling, 2012, comes, across, rather, rough, tannic, rustic, earthy, herbal, characteristics, nonetheless, think, pleasantly, unfussy, country, wine, good, companion, hearty, winter, stew) 5 15.0 87 Spain Michael Schachner Tempranillo-Merlot blackberry and raspberry aromas show a typical navarran whiff of green herbs and, in this case, horseradish. in the mouth, this is fairly full bodied, with tomatoey acidity. spicy, herbal flavors complement dark plum fruit, while the finish is fresh but grabby. List(blackberry, and, raspberry, aromas, show, a, typical, navarran, whiff, of, green, herbs, and, in, this, case, horseradish, in, the, mouth, this, is, fairly, full, bodied, with, tomatoey, acidity, spicy, herbal, flavors, complement, dark, plum, fruit, while, the, finish, is, fresh, but, grabby) List(blackberry, raspberry, aromas, show, typical, navarran, whiff, green, herbs, case, horseradish, mouth, fairly, full, bodied, tomatoey, acidity, spicy, herbal, flavors, complement, dark, plum, fruit, finish, fresh, grabby) 6 16.0 87 Italy Kerin O’Keefe Frappato here's a bright, informal red that opens with aromas of candied berry, white pepper and savory herb that carry over to the palate. it's balanced with fresh acidity and soft tannins. List(here, s, a, bright, informal, red, that, opens, with, aromas, of, candied, berry, white, pepper, and, sa

In [20]:
#two hyper parameters needed to be tuned
#hashingTF = HashingTF(inputCol="filtered", outputCol="rawFeatures",numFeatures=5000)
hashingTF = HashingTF(inputCol="filtered", outputCol="rawFeatures", numFeatures=5000)
idf = IDF(inputCol="rawFeatures", outputCol="tf_idf_features", minDocFreq=0)

In [21]:
word2vec = Word2Vec(vectorSize = 300, minCount = 5, inputCol = 'filtered', outputCol = 'word2vec_features')

In [22]:
stopWords_removed=stopwordsRemover.transform(wordsData)
# Define NGram transformer
ngram = NGram(n=2, inputCol="filtered", outputCol="bigrams")

# Create bigram_df as a transform of unigram_df using NGram tranformer
production_df = ngram.transform(stopWords_removed)
production_df = production_df.where(size(col("bigrams")) >= 2)
word2vec_bigram = Word2Vec(vectorSize = 300, minCount = 5, inputCol = 'bigrams', outputCol = 'bigram_features')

Category feature: Use Points and classify points into the following categories  
Wine Enthusiast's 100-point wine-scoring scale:
  - 98–100 – Classic
  - 94–97 – Superb
  - 90–93 – Excellent
  - 87–89 – Very good
  - 83–86 – Good
  - 80–82 – Acceptable  


Reference  
https://www.wine-searcher.com/critics-17-wine+enthusiast

In [24]:
splits_6 = [80,83, 87,90, 94,98,100]
splits_3 = [80,87,94,100]
bucketizer_3 = Bucketizer(splits=splits_3, inputCol="points", outputCol="label")
bucketizer_6 = Bucketizer(splits=splits_6, inputCol="points", outputCol="label_6")

In [25]:
cols = ['country', 'taster_name','variety']

indexers = [
    StringIndexer(inputCol=c, outputCol="{0}_indexed".format(c), handleInvalid="keep")
    for c in cols
]

encoder = OneHotEncoderEstimator(
    inputCols=[indexer.getOutputCol() for indexer in indexers],
    outputCols=[
        "{0}_encoded".format(indexer.getOutputCol()) for indexer in indexers]
)

# assemble all 4 columns (country, tastername, variety and price)
assembler_num_cat = VectorAssembler(
    inputCols=['country_indexed_encoded','taster_name_indexed_encoded','variety_indexed_encoded','price'],
    outputCol="num_cat_features"
)

assembler_combine = VectorAssembler(
    inputCols=['num_cat_features', 'tf_idf_features'],
    outputCol="combine_features"
)

assembler_combine_w2v=VectorAssembler(
    inputCols=['num_cat_features', 'word2vec_features'],
    outputCol="combine_features_w2v"
)
assembler_combine_bigram=VectorAssembler(
    inputCols=['num_cat_features', 'bigram_features'],
    outputCol="combine_features_bigram"
)

In [26]:
chi_selector = ChiSqSelector(numTopFeatures=1000, featuresCol="combine_features",
                         outputCol="selectedFeatures", labelCol="label")

In [27]:
pipeline = Pipeline(stages=[regexTokenizer, stopwordsRemover, hashingTF, idf, bucketizer_3, bucketizer_6]+ indexers+ [encoder, assembler_num_cat, assembler_combine, chi_selector])
pipelineFit = pipeline.fit(df_lower)
dataset = pipelineFit.transform(df_lower).select('id', 'tf_idf_features',  'num_cat_features', 'combine_features', "selectedFeatures", 'label')

In [28]:
#dataset for regression
pipeline = Pipeline(stages=[regexTokenizer, stopwordsRemover, hashingTF, idf, bucketizer_3, bucketizer_6]+ indexers+ [encoder, assembler_num_cat, assembler_combine, chi_selector])
pipelineFit = pipeline.fit(df_lower)
rdataset=pipelineFit.transform(df_lower).select('id', 'tf_idf_features',  'num_cat_features', 'combine_features', "selectedFeatures", "points")

In [29]:
pipeline_w2v = Pipeline(stages=[regexTokenizer, stopwordsRemover, word2vec, bucketizer_3, bucketizer_6]+ indexers+ [encoder, assembler_num_cat, assembler_combine_w2v])
pipelineFit_w2v = pipeline_w2v.fit(df_lower)
dataset_w2v = pipelineFit_w2v.transform(df_lower).select('id', 'word2vec_features',  'num_cat_features', 'combine_features_w2v',  'label')

In [30]:
#for regression
pipeline_w2v = Pipeline(stages=[regexTokenizer, stopwordsRemover, word2vec, bucketizer_3, bucketizer_6]+ indexers+ [encoder, assembler_num_cat, assembler_combine_w2v])
pipelineFit_w2v = pipeline_w2v.fit(df_lower)
rdataset_w2v = pipelineFit_w2v.transform(df_lower).select('id', 'word2vec_features',  'num_cat_features', 'combine_features_w2v',  'points')

In [31]:
pipeline_bigram = Pipeline(stages=[regexTokenizer, stopwordsRemover, ngram, word2vec_bigram, bucketizer_3, bucketizer_6]+ indexers+ [encoder, assembler_num_cat, assembler_combine_bigram])
pipelineFit_bigram = pipeline_bigram.fit(df_lower)
dataset_bigram = pipelineFit_bigram.transform(df_lower).select('id', 'bigram_features',  'num_cat_features', 'combine_features_bigram',  'label')

In [32]:
#for regression
pipeline_bigram = Pipeline(stages=[regexTokenizer, stopwordsRemover, ngram, word2vec_bigram, bucketizer_3, bucketizer_6]+ indexers+ [encoder, assembler_num_cat, assembler_combine_bigram])
pipelineFit_bigram = pipeline_bigram.fit(df_lower)
rdataset_bigram = pipelineFit_bigram.transform(df_lower).select('id', 'bigram_features',  'num_cat_features', 'combine_features_bigram',  'points')

In [33]:
display(dataset)

id tf_idf_features num_cat_features combine_features selectedFeatures label 1 List(0, 5000, List(200, 808, 941, 1201, 1469, 1800, 2203, 2390, 2697, 2779, 2878, 2891, 3057, 3389, 3414, 3894, 3921, 4291, 4313, 4724, 4783), List(1.362117655660329, 4.087561298968214, 4.2633003296607095, 5.478301209518669, 2.1284318631636596, 3.1364954033713417, 2.09072756407599, 2.6051282112005003, 0.7246939478854219, 3.715674890560556, 5.07349638535658, 1.4871925422057322, 4.122670220849488, 1.6457501176023361, 4.971841538311946, 2.683195627994554, 2.563585715251706, 1.9083502488276456, 3.2325484332779215, 2.2801535886755144, 6.264780329870833)) List(0, 753, List(4, 42, 75, 752), List(1.0, 1.0, 1.0, 15.0)) List(0, 5753, List(4, 42, 75, 752, 953, 1561, 1694, 1954, 2222, 2553, 2956, 3143, 3450, 3532, 3631, 3644, 3810, 4142, 4167, 4647, 4674, 5044, 5066, 5477, 5536), List(1.0, 1.0, 1.0, 15.0, 1.362117655660329, 4.087561298968214, 4.2633003296607095, 5.478301209518669, 2.1284318631636596, 3.1364954033713417, 2.09072756407599, 2.6051282112005003, 0.7246939478854219, 3.715674890560556, 5.07349638535658, 1.4871925422057322, 4.122670220849488, 1.6457501176023361, 4.971841538311946, 2.683195627994554, 2.563585715251706, 1.9083502488276456, 3.2325484332779215, 2.2801535886755144, 6.264780329870833)) List(0, 1000, List(12, 57, 103, 229, 251, 362, 423, 490, 524, 584, 621, 622, 647, 699, 795, 803, 877, 950), List(1.0, 15.0, 1.362117655660329, 4.087561298968214, 4.2633003296607095, 2.1284318631636596, 3.1364954033713417, 2.09072756407599, 2.6051282112005003, 0.7246939478854219, 5.07349638535658, 1.4871925422057322, 4.122670220849488, 1.6457501176023361, 2.683195627994554, 2.563585715251706, 3.2325484332779215, 2.2801535886755144)) 1.0 2 List(0, 5000, List(22, 200, 409, 571, 625, 927, 977, 1062, 1069, 1320, 1783, 2273, 2697, 2711, 2756, 3658, 3689), List(4.750130994169161, 1.362117655660329, 1.4946199448192523, 2.982725603381101, 2.5661658069861444, 3.455639586048799, 2.343926862768019, 4.7491754279234915, 4.467961218479197, 3.2580221095699318, 3.8334579262169393, 4.769436613063314, 0.7246939478854219, 4.470126502616414, 7.85271203708397, 5.109815104651592, 3.135734078629582)) List(0, 753, List(0, 46, 80, 752), List(1.0, 1.0, 1.0, 14.0)) List(0, 5753, List(0, 46, 80, 752, 775, 953, 1162, 1324, 1378, 1680, 1730, 1815, 1822, 2073, 2536, 3026, 3450, 3464, 3509, 4411, 4442), List(1.0, 1.0, 1.0, 14.0, 4.750130994169161, 1.362117655660329, 1.4946199448192523, 2.982725603381101, 2.5661658069861444, 3.455639586048799, 2.343926862768019, 4.7491754279234915, 4.467961218479197, 3.2580221095699318, 3.8334579262169393, 4.769436613063314, 0.7246939478854219, 4.470126502616414, 7.85271203708397, 5.109815104651592, 3.135734078629582)) List(0, 1000, List(0, 16, 57, 103, 146, 191, 260, 275, 331, 584, 587, 758), List(1.0, 1.0, 14.0, 1.362117655660329, 1.4946199448192523, 2.5661658069861444, 2.343926862768019, 4.467961218479197, 3.2580221095699318, 0.7246939478854219, 4.470126502616414, 3.135734078629582)) 1.0 3 List(0, 5000, List(1, 52, 218, 542, 875, 927, 948, 996, 1069, 1446, 1529, 1632, 2146, 2245, 2634, 3011, 3297, 3309, 3813, 3941, 4159, 4400), List(3.189272942971903, 5.053875088769252, 4.54201373212973, 6.966661190399533, 3.940263590253959, 3.455639586048799, 1.957079082287936, 4.96826797882108, 4.467961218479197, 3.0712669070692953, 4.659699722805689, 3.1516515687905136, 5.607035076361804, 4.234917306508176, 1.1716705047730245, 3.421641977507379, 1.2091716701318462, 2.6506947017837224, 2.551738626477817, 1.2855908346662772, 3.3748917804885403, 4.33641449046643)) List(0, 753, List(0, 57, 66, 752), List(1.0, 1.0, 1.0, 13.0)) List(0, 5753, List(0, 57, 66, 752, 754, 805, 971, 1295, 1628, 1680, 1701, 1749, 1822, 2199, 2282, 2385, 2899, 2998, 3387, 3764, 4050, 4062, 4566, 4694, 4912, 5153), List(1.0, 1.0, 1.0, 13.0, 3.189272942971903, 5.053875088769252, 4.54201373212973, 6.966661190399533, 3.940263590253959, 3.455639586048799, 1.957079082287936, 4.96826797882108, 4.4679612184791

In [34]:
display(dataset_w2v )

id word2vec_features num_cat_features combine_features_w2v label 1 List(1, 300, List(), List(0.10003704054369812, 0.010672187432646751, 0.05351976036936754, 0.04102427878838387, 0.056833786047285506, 0.03014047410605209, -0.055164197443186166, -0.047182172442609, 0.02058481185563973, 0.04347957376324172, -0.11053741568078597, -0.07046027071330518, -0.0678580409093272, -0.08578420071197407, 0.0366415166562157, -8.65007240680002E-4, 0.019506053910368963, 0.03726203899298395, -0.023710696026682854, -0.08942415300268856, 0.07777174012291999, 0.07575614173852262, 0.06474340918828689, -0.03799710141140081, 0.07677972002974932, -0.012437878708754267, -0.011928451369472202, 0.02830045719054483, 0.017625097096675917, 0.04619392668384881, -0.03337114133561651, -0.06318436252574125, -0.041135863500780294, -0.01701783692641627, -0.10111450678890659, 0.10320679062888735, 0.04021925687612522, -0.008993118325070965, 0.022529939278250647, 0.026201041947518076, 0.03271901320909992, 0.006770134471090776, -0.07232737727463245, 0.020048374576228004, 0.024843430723107997, -0.043188077364382994, -0.009696923950243564, 0.0273998995488953, 0.0033502370850848296, 5.596105253235215E-4, 0.04510052180350092, -0.04166348651051521, 0.0578173191641413, -0.06019563423026175, -0.07238202644622929, 0.03481100016229209, 0.09704225403921944, -0.11499593001125114, 0.02615233075006732, -0.030808203864753955, 0.021628723568504763, -0.03559592370653436, 0.08334105887583323, -0.0761605205590881, 0.010689815705908197, -0.09060448057772148, 0.06136949546635151, -0.013548933058267548, 0.012767863814674672, 0.031713416711205526, 0.06358269628669534, -0.04440585874198448, 0.031585173459634894, 0.008347237970502602, 0.050743656691684874, 0.033669921303434026, 0.07629672735042514, 0.0498764044826939, -0.0433738398853512, 0.04432049591005558, 0.07273839775561576, -0.010063907896567668, -0.07123811794666662, -0.0434534696507312, -0.03649791727019917, 0.006025981024972029, -0.06103728068549008, 0.041347446984478405, -0.02511710405261034, 0.05358485258849603, -0.00604018927108319, 0.025056506107960428, -0.03978884340315181, -0.018285569291384446, -0.027727161001946242, -0.059256479055398985, -0.05228984967938491, 0.10057517125581701, 0.04534208676999523, 0.01491577004725557, 0.03872963984862768, -0.10207350809304487, 0.010846151837280818, 0.04289918078575283, -0.013781091453330147, 0.0016872857342518511, 0.04047360426158688, 0.01912439933844975, -0.007415877322533301, 0.04978483658106554, -0.04343050838048969, -0.11148928757756948, 0.07477071548679044, 0.05728073077764184, 0.09123449298065332, 0.05800435896075907, -0.098755024351357, 0.04186218937060662, 0.023228882634568782, -0.007957590422371314, 0.002089412849662559, 0.06777284533849784, -0.0709663080176272, -0.03985318896316346, -0.04413932354267065, -0.03234319485324834, -0.049139733958457193, 0.13231605965466725, -0.004377615904169423, -0.031155441798979326, 0.02809817911613555, 0.012562697513550075, -0.032491970352739805, 0.06015464184539658, 0.03484533159505753, 0.047516616549165475, 0.03696525815342153, 0.003949309034006936, -0.047334509036902866, 0.027478761011956346, 0.02118971495933476, -0.010136815586260386, 0.04336251919379546, -0.030714566952415874, 0.038873285188206604, -0.015818344639791617, 0.019204241345592198, -0.0616012169491677, -0.03571925412065216, -0.02240750800064277, 0.030308057814614757, -0.037683122081770784, 0.1005430812947452, 0.03417370885255791, 0.01290082338354772, -0.15141261901174272, 0.009789280282954374, -0.008911119624307113, -0.03494383740637983, -0.04628348423700247, 0.1611245230195068, -0.10738943653580332, 0.013340078981681948, -0.04842440685301664, -0.0710875455157033, -0.08532873859318593, 0.04380516424065544, 0.036999155035508526, 0.08370823575006354, 0.13704748850847992, 0.026551054912574944, 0.02136027259569216, -0.061596998013556004, 0.08145259845159238, -0.04607324971861782, -0.015800909460743976, -0.02084469416045717, 0.015959991763035454, -0.0631654349022678, 0.102081846268404

In [35]:
display(rdataset_bigram )

id bigram_features num_cat_features combine_features_bigram points 1 List(1, 300, List(), List(-0.007369368344370741, 0.04087281093234196, -0.025894493237137797, -0.008129757852293551, -0.044306883309036496, -0.025515028694644573, -0.010729676700429992, 0.01709271795843961, 0.0012540930300019683, 0.040183186461217706, 0.0010607792297378184, 0.0480228495085612, 0.038210273999720816, 0.008532937860582025, -0.011591986066196115, 0.021674721511953977, 0.06627403455204331, -0.026856097216659693, -0.0584287992794998, -0.0202324433834292, 0.016726169898174704, -0.04093932032119483, -0.022941391705535354, -0.028965137875638904, -0.05081481891684234, 0.00473896341281943, -0.07068595545715653, -0.11852571731433273, 0.02920721578557277, 8.578925160691143E-4, 0.002576117269927636, -0.0015426924685016275, -0.05779740770813078, 0.010303404531441629, 0.019829993932216895, -0.02854937850133865, 0.014719456146121957, 0.03338642290327698, -0.0854473416111432, -0.0058516273507848385, -0.007215953733248171, -0.08677499468903989, -0.02387924350332469, -0.014827213739044965, 0.06777585036470556, 0.019102350575849414, -0.023067306773737074, -0.07831187791889534, 0.08384775302547497, 0.01829826079774648, -0.004164398371358402, 0.014999533919035458, 0.04544728950131685, 0.008277934021316468, -0.028567798971198502, -0.00792311301920563, -0.062254530489735775, 0.026813182450132447, 0.06575343355361839, -0.02074194400338456, -0.06737383774307092, 0.0084505753882695, 0.03560805629240349, 0.033824277902022006, -0.035687092668376864, -0.026345464889891448, -0.0037797733442857862, -0.019017278659157456, -0.06841217547189445, -0.015366373932920396, 0.024613407463766637, -0.06466192816442344, 0.056696458254009485, -0.07316568132955581, -0.0017796186963096262, -0.037165914132492615, -0.030221746650931892, -0.05199760147370398, 0.01092472946329508, -0.0063661966705694795, -0.03566537164151669, -0.03896075674565509, 0.04797663622302935, -0.007222110655857251, -0.016348491329699757, -0.00750294293393381, -0.05360084843705409, -0.007021006400464103, -0.10503303327132017, 0.004398327053058893, 0.03061911890981719, 0.010248508583754302, 0.005397628390346654, 0.01072438761475496, 0.016768774949014187, 0.02126817784301238, -0.017395881783158984, 0.033888413081876935, -0.011888844729401172, -0.024364142725244165, 0.029193115036468955, 0.0476949479430914, 0.047656117918086244, 0.015358379879035057, 0.023876918270252647, 0.05095010126242414, -0.002693820290733129, 3.365078242495656E-4, -0.037641480960883204, -0.06498364359140396, -0.007054408814292402, 0.05181888164952397, 0.02710731299594045, -0.1157914492301643, -0.07979024902451784, 0.004245938907843083, 0.011369840597035365, 0.004217309027444572, -0.004172200930770487, -0.00854193818231579, 0.05140066386666149, 0.05981085984967649, -0.017159325326792898, -0.020868526306003332, 0.03860863877926022, -0.04219997306936421, 0.08252102441620082, 0.023412994155660272, -0.005686760833486915, -0.01974485608516261, 0.015213164302986117, 0.05325044714845717, 0.03684052210301161, 0.011808243022096578, -0.01652926338138059, -0.0425033757230267, 0.049685214426426684, 0.04894883878296241, -0.005353598308283836, 0.013437195401638747, 0.09431604670826346, -0.00839809172321111, -0.1278456279891543, -0.026555014289624524, -0.003913845820352435, -0.03153954788576812, 0.01821173166681547, 3.5261220764368776E-4, -0.05222654201788828, -0.04186735463154037, 9.731757774716244E-4, -0.011363904119934888, 0.03256849109893665, -0.09354498353786767, -0.012178750848397613, -0.07881864320952446, -0.010962575121084228, -0.026610252261161805, -0.043196248053573076, -0.02635450753150508, -0.010253891145111993, 0.061566559900529685, -0.003928339062258601, 0.002135609369724989, -0.005306906119221822, -0.03461531096836552, -0.05156671286094934, 0.01178154975641519, 0.0398300108499825, -0.010217874922091141, 0.02088912678009365, -0.08092077950714156, -0.014434252586215736, -0.05924926299485378, -0.010189749146229589, -0.026592759357299656, 0.06315812673419

## 4. Model Exploration

In [37]:
(trainingData, testData) = dataset.randomSplit([0.8, 0.2], seed = 100)
(rtrainingData, rtestData) = rdataset.randomSplit([0.8, 0.2], seed = 100) #for regression
print("Training Dataset Count: " + str(trainingData.count()))
print("Test Dataset Count: " + str(testData.count()))

Training Dataset Count: 96685
Test Dataset Count: 24231

In [38]:
# Training and testing splitting for word2vec
(trainingData_w2v, testData_w2v) = dataset_w2v.randomSplit([0.8, 0.2], seed = 100)
(rtrainingData_w2v, rtestData_w2v) = rdataset_w2v.randomSplit([0.8, 0.2], seed = 100) #for regression
print("Training Dataset Count: " + str(trainingData_w2v.count()))
print("Test Dataset Count: " + str(testData_w2v.count()))

Training Dataset Count: 96685
Test Dataset Count: 24231

In [39]:
# Training and testing splitting for bigram
(trainingData_bigram, testData_bigram) = dataset_bigram.randomSplit([0.8, 0.2], seed = 100)
(rtrainingData_bigram, rtestData_bigram) = rdataset_bigram.randomSplit([0.8, 0.2], seed = 100)#for regression
print("Training Dataset Count: " + str(trainingData_bigram.count()))
print("Test Dataset Count: " + str(testData_bigram.count()))

Training Dataset Count: 96685
Test Dataset Count: 24231

In [40]:
evaluator_f1 = MulticlassClassificationEvaluator(predictionCol="prediction", metricName='f1')
evaluator_acc = MulticlassClassificationEvaluator(predictionCol="prediction", metricName='accuracy')
evaluator_recall = MulticlassClassificationEvaluator(predictionCol="prediction", metricName='weightedRecall')
evaluator_precision = MulticlassClassificationEvaluator(predictionCol="prediction", metricName='weightedPrecision')

In [41]:
lr_tf_idf = LogisticRegression(featuresCol='tf_idf_features')
lr_tf_idf_Model = lr_tf_idf.fit(trainingData)
lr_tf_idf_predictions = lr_tf_idf_Model.transform(testData)

lr_num_cat = LogisticRegression(featuresCol='num_cat_features')
lr_num_cat_Model = lr_num_cat.fit(trainingData)
lr_num_cat_predictions = lr_num_cat_Model.transform(testData)

lr_combine = LogisticRegression(featuresCol='combine_features')
lr_combine_Model = lr_combine.fit(trainingData)
lr_combine_predictions = lr_combine_Model.transform(testData)

lr_selected = LogisticRegression(featuresCol='selectedFeatures')
lr_selected_Model = lr_selected.fit(trainingData)
lr_selected_predictions = lr_selected_Model.transform(testData)


In [42]:
# For w2v model
lr_w2v = LogisticRegression(featuresCol='word2vec_features')
lr_Model_w2v = lr_w2v.fit(trainingData_w2v)
lr_predictions_w2v = lr_Model_w2v.transform(testData_w2v)

lr_num_cat = LogisticRegression(featuresCol='num_cat_features')
lr_num_cat_Model = lr_num_cat.fit(trainingData)
lr_num_cat_predictions = lr_num_cat_Model.transform(testData)

lr_combine_w2v = LogisticRegression(featuresCol='combine_features_w2v')
lr_combine_Model_w2v = lr_combine_w2v.fit(trainingData_w2v)
lr_combine_predictions_w2v = lr_combine_Model_w2v.transform(testData_w2v)


# For bigram w2v
lr_bigram = LogisticRegression(featuresCol='bigram_features')
lr_Model_bigram = lr_bigram.fit(trainingData_bigram)
lr_predictions_bigram = lr_Model_bigram.transform(testData_bigram)

lr_num_cat = LogisticRegression(featuresCol='num_cat_features')
lr_num_cat_Model = lr_num_cat.fit(trainingData)
lr_num_cat_predictions = lr_num_cat_Model.transform(testData)

lr_combine_bigram = LogisticRegression(featuresCol='combine_features_bigram')
lr_combine_Model_bigram = lr_combine_bigram.fit(trainingData_bigram)
lr_combine_predictions_bigram = lr_combine_Model_bigram.transform(testData_bigram)


In [43]:
def print_eval_tf_idf(metrics,num_cat,combine, selected,name_of_feature):
  print(name_of_feature)
  print('f1: ' + str(evaluator_f1.evaluate(metrics)))
  print('acc: ' + str(evaluator_acc.evaluate(metrics)))
  print('recall: ' + str(evaluator_recall.evaluate(metrics)))
  print('precision' + str(evaluator_precision.evaluate(metrics)))
  print('num_cat_features')
  print('f1: ' + str(evaluator_f1.evaluate(num_cat)))
  print('acc: ' + str(evaluator_acc.evaluate(num_cat)))
  print('recall: ' + str(evaluator_recall.evaluate(num_cat)))
  print('precision: ' + str(evaluator_precision.evaluate(num_cat)))
  print('combine_features')
  print('f1: ' + str(evaluator_f1.evaluate(combine)))
  print('acc: ' + str(evaluator_acc.evaluate(combine)))
  print('recall: ' + str(evaluator_recall.evaluate(combine)))
  print('precision: ' + str(evaluator_precision.evaluate(combine)))
  print('selectedFeatures')
  print('f1: ' + str(evaluator_f1.evaluate(selected)))
  print('acc: ' + str(evaluator_acc.evaluate(selected)))
  print('recall: ' + str(evaluator_recall.evaluate(selected)))
  print('precision: ' + str(evaluator_precision.evaluate(selected)))

In [44]:
def print_eval_w2v(metrics,combine, name_of_feature):
  print(name_of_feature)
  print('f1: ' + str(evaluator_f1.evaluate(metrics)))
  print('acc: ' + str(evaluator_acc.evaluate(metrics)))
  print('recall: ' + str(evaluator_recall.evaluate(metrics)))
  print('precision' + str(evaluator_precision.evaluate(metrics)))
  
  print('combine_features')
  print('f1: ' + str(evaluator_f1.evaluate(combine)))
  print('acc: ' + str(evaluator_acc.evaluate(combine)))
  print('recall: ' + str(evaluator_recall.evaluate(combine)))
  print('precision: ' + str(evaluator_precision.evaluate(combine)))

In [45]:
print_eval_tf_idf(lr_tf_idf_predictions, lr_num_cat_predictions, lr_combine_predictions, lr_selected_predictions,'tf_idf_features')

tf_idf_features
f1: 0.7967906073786456
acc: 0.800998720647105
recall: 0.800998720647105
precision0.7947831910018713
num_cat_features
f1: 0.720815350710597
acc: 0.7436754570591391
recall: 0.7436754570591392
precision: 0.7291310863779568
combine_features
f1: 0.8199633138722684
acc: 0.8220874086913458
recall: 0.8220874086913458
precision: 0.8186942005375674
selectedFeatures
f1: 0.8261909428906107
acc: 0.8315381123354381
recall: 0.8315381123354381
precision: 0.8265029265148076

In [46]:
print_eval_w2v(lr_predictions_w2v, lr_combine_predictions_w2v,'word2vec_features')

word2vec_features
f1: 0.7771492903952112
acc: 0.7951384589988032
recall: 0.7951384589988033
precision0.7796311437466886
combine_features
f1: 0.8150617756512754
acc: 0.82349056993108
recall: 0.8234905699310799
precision: 0.816604665941819

In [47]:
print_eval_w2v(lr_predictions_bigram, lr_combine_predictions_bigram,'bigram_features')

bigram_features
f1: 0.6630332582242735
acc: 0.7137963765424457
recall: 0.7137963765424457
precision0.6740483347519062
combine_features
f1: 0.7514167042121048
acc: 0.7662498452395692
recall: 0.7662498452395692
precision: 0.7546078310242577

In [48]:
from pyspark.ml.classification import LinearSVC
lsvc = LinearSVC(maxIter=5, regParam=0.01)
svm_tf_idf=OneVsRest(featuresCol='tf_idf_features',classifier=lsvc)
svm_tf_idf_Model = svm_tf_idf.fit(trainingData)
svm_tf_idf_predictions = svm_tf_idf_Model.transform(testData)

svm_num_cat =OneVsRest(featuresCol='num_cat_features',classifier=lsvc)
svm_num_cat_Model = svm_num_cat.fit(trainingData)
svm_num_cat_predictions = svm_num_cat_Model.transform(testData)

svm_combine  =OneVsRest(featuresCol='combine_features',classifier=lsvc)
svm_combine_Model = svm_combine.fit(trainingData)
svm_combine_predictions = svm_combine_Model.transform(testData)

svm_selected  =OneVsRest(featuresCol='selectedFeatures',classifier=lsvc)
svm_selected_Model = svm_selected.fit(trainingData)
svm_selected_predictions = svm_selected_Model.transform(testData)

In [49]:
# SVM for w2v model

svm_w2v =OneVsRest(featuresCol='word2vec_features',classifier=lsvc)
svm_Model_w2v = svm_w2v.fit(trainingData_w2v)
svm_predictions_w2v = svm_Model_w2v.transform(testData_w2v)


svm_combine_w2v = OneVsRest(featuresCol='combine_features_w2v',classifier=lsvc)
svm_combine_Model_w2v = svm_combine_w2v.fit(trainingData_w2v)
svm_combine_predictions_w2v = svm_combine_Model_w2v.transform(testData_w2v)


In [50]:
# SVM for bigram model

svm_bigram = OneVsRest(featuresCol='bigram_features',classifier=lsvc)
svm_Model_bigram = svm_bigram.fit(trainingData_bigram)
svm_predictions_bigram = svm_Model_bigram.transform(testData_bigram)

svm_combine_bigram =  OneVsRest(featuresCol='combine_features_bigram',classifier=lsvc)
svm_combine_Model_bigram = svm_combine_bigram.fit(trainingData_bigram)
svm_combine_predictions_bigram = svm_combine_Model_bigram.transform(testData_bigram)


In [51]:
print_eval_tf_idf(svm_tf_idf_predictions, svm_num_cat_predictions, svm_combine_predictions, svm_selected_predictions,'tf_idf_features')

tf_idf_features
f1: 0.7310080594091766
acc: 0.7717799513020511
recall: 0.771779951302051
precision0.7468207415130942
num_cat_features
f1: 0.5653365268870383
acc: 0.6861458462300359
recall: 0.6861458462300359
precision: 0.656862748841087
combine_features
f1: 0.6616868731347996
acc: 0.7336882505880896
recall: 0.7336882505880896
precision: 0.7419768080331495
selectedFeatures
f1: 0.7325350163258667
acc: 0.7712847179233213
recall: 0.7712847179233213
precision: 0.7423612194216348

In [52]:
print_eval_w2v(svm_predictions_w2v, svm_combine_predictions_w2v,'word2vec_features')

word2vec_features
f1: 0.5645935509014965
acc: 0.6873426602286328
recall: 0.6873426602286328
precision0.7229020678755627
combine_features
f1: 0.5674816438799706
acc: 0.6886220131236845
recall: 0.6886220131236845
precision: 0.7271174691690233

In [53]:
print_eval_w2v(svm_predictions_bigram, svm_combine_predictions_bigram,'bigram_features')

bigram_features
f1: 0.5603401098676104
acc: 0.6848252238867566
recall: 0.6848252238867567
precision0.6634893927481944
combine_features
f1: 0.5591014759958384
acc: 0.6847426849903017
recall: 0.6847426849903017
precision: 0.6817301369178967

In [54]:
rf_tf_idf = RandomForestClassifier(featuresCol='tf_idf_features')
rf_tf_idf_Model = rf_tf_idf.fit(trainingData)
rf_tf_idf_predictions = rf_tf_idf_Model.transform(testData)

rf_num_cat = RandomForestClassifier(featuresCol='num_cat_features')
rf_num_cat_Model = rf_num_cat.fit(trainingData)
rf_num_cat_predictions = rf_num_cat_Model.transform(testData)

rf_combine = RandomForestClassifier(featuresCol='combine_features')
rf_combine_Model = rf_combine.fit(trainingData)
rf_combine_predictions = rf_combine_Model.transform(testData)

rf_selected = RandomForestClassifier(featuresCol='selectedFeatures')
rf_selected_Model = rf_selected.fit(trainingData)
rf_selected_predictions = rf_selected_Model.transform(testData)

In [55]:
# Random forest model for w2v metrics
rf_w2v = RandomForestClassifier(featuresCol='word2vec_features')
rf_Model_w2v = rf_w2v.fit(trainingData_w2v)
rf_predictions_w2v = rf_Model_w2v.transform(testData_w2v)

rf_num_cat = RandomForestClassifier(featuresCol='num_cat_features')
rf_num_cat_Model = rf_num_cat.fit(trainingData)
rf_num_cat_predictions = rf_num_cat_Model.transform(testData)

rf_combine_w2v = RandomForestClassifier(featuresCol='combine_features_w2v')
rf_combine_Model_w2v = rf_combine_w2v.fit(trainingData_w2v)
rf_combine_predictions_w2v = rf_combine_Model_w2v.transform(testData_w2v)

In [56]:
# Random forest model for binary w2v metrics
rf_bigram = RandomForestClassifier(featuresCol='bigram_features')
rf_Model_bigram = rf_bigram.fit(trainingData_bigram)
rf_predictions_bigram = rf_Model_bigram.transform(testData_bigram)

rf_num_cat = RandomForestClassifier(featuresCol='num_cat_features')
rf_num_cat_Model = rf_num_cat.fit(trainingData)
rf_num_cat_predictions = rf_num_cat_Model.transform(testData)

rf_combine_bigram = RandomForestClassifier(featuresCol='combine_features_bigram')
rf_combine_Model_bigram = rf_combine_bigram.fit(trainingData_bigram)
rf_combine_predictions_bigram = rf_combine_Model_bigram.transform(testData_bigram)


In [57]:
print_eval_tf_idf(rf_tf_idf_predictions, rf_num_cat_predictions, rf_combine_predictions, rf_combine_predictions,'tf_idf_features')

tf_idf_features
f1: 0.554686671794674
acc: 0.6832569848541125
recall: 0.6832569848541125
precision0.4668401073519329
num_cat_features
f1: 0.554686671794674
acc: 0.6832569848541125
recall: 0.6832569848541125
precision: 0.4668401073519329
combine_features
f1: 0.554686671794674
acc: 0.6832569848541125
recall: 0.6832569848541125
precision: 0.4668401073519329
selectedFeatures
f1: 0.554686671794674
acc: 0.6832569848541125
recall: 0.6832569848541125
precision: 0.4668401073519329

In [58]:
print_eval_w2v(rf_predictions_w2v, rf_combine_predictions_w2v,'word2vec_features')

word2vec_features
f1: 0.6775249697282529
acc: 0.7374437703767901
recall: 0.73744377037679
precision0.7192552361275555
combine_features
f1: 0.6632721308992775
acc: 0.7316660476249432
recall: 0.7316660476249432
precision: 0.7242682692279107

In [59]:
print_eval_w2v(rf_predictions_bigram, rf_combine_predictions_bigram,'bigram_features')

bigram_features
f1: 0.5889475851019784
acc: 0.6931203829804795
recall: 0.6931203829804796
precision0.6617732733850532
combine_features
f1: 0.5838457761008388
acc: 0.693945771945029
recall: 0.693945771945029
precision: 0.6930798395041777

In [60]:
layers = [1000, 100,100,100,3]

# create the trainer and set its parameters
MLPC_trainer = MultilayerPerceptronClassifier(maxIter=500, layers=layers, blockSize=128, seed=1234, featuresCol='selectedFeatures')

# train the model
MLPC_model = MLPC_trainer.fit(trainingData)

# compute accuracy on the test set
predictions = MLPC_model.transform(testData)

In [61]:
print('MLPC')
print('f1: ' + str(evaluator_f1.evaluate(predictions)))
print('acc: ' + str(evaluator_acc.evaluate(predictions)))
print('recall: ' + str(evaluator_recall.evaluate(predictions)))
print('precision: ' + str(evaluator_precision.evaluate(predictions)))

MLPC
f1: 0.8300658209060542
acc: 0.8332714291609922
recall: 0.8332714291609921
precision: 0.8289634483309992

In [62]:
from pyspark.ml.regression import GBTRegressor

#tf-idf
gbtr_tf_idf = GBTRegressor(maxIter=10, maxDepth=10,featuresCol='tf_idf_features',labelCol='points',seed=42)
gbtr_tf_idf_model = gbtr_tf_idf.fit(rtrainingData)
gbtr_tf_idf_predictions = gbtr_tf_idf_model.transform(rtestData)

gbtr_num_cat = GBTRegressor(maxIter=10, maxDepth=10,featuresCol='num_cat_features',labelCol='points',seed=42)
gbtr_num_cat_model = gbtr_num_cat.fit(rtrainingData)
gbtr_num_cat_predictions = gbtr_num_cat_model.transform(rtestData)

gbtr_com = GBTRegressor(maxIter=10, maxDepth=10,featuresCol='combine_features',labelCol='points',seed=42)
gbtr_com_model = gbtr_com.fit(rtrainingData)
gbtr_com_predictions = gbtr_com_model.transform(rtestData)

gbtr_selected= GBTRegressor(maxIter=10, maxDepth=10,featuresCol='selectedFeatures',labelCol='points',seed=42)
gbtr_selected_model = gbtr_selected.fit(rtrainingData)
gbtr_selected_predictions = gbtr_selected_model.transform(rtestData)




In [63]:
# For w2v model
gbtr_w2v = GBTRegressor(maxIter=10, maxDepth=10,featuresCol='word2vec_features',labelCol='points',seed=42)
gbtr_w2v_model = gbtr_w2v.fit(rtrainingData_w2v)
gbtr_w2v_predictions = gbtr_w2v_model.transform(rtestData_w2v)

gbtr_w2v_com = GBTRegressor(maxIter=10, maxDepth=10,featuresCol='combine_features_w2v',labelCol='points',seed=42)
gbtr_w2v_com_model = gbtr_w2v_com.fit(rtrainingData_w2v)
gbtr_w2v_com_predictions = gbtr_w2v_com_model.transform(rtestData_w2v)

# For bigram 
gbtr_bg = GBTRegressor(maxIter=10, maxDepth=10,featuresCol='bigram_features',labelCol='points',seed=42)
gbtr_bg_model = gbtr_bg.fit(rtrainingData_bigram)
gbtr_bg_predictions = gbtr_bg_model.transform(rtestData_bigram)

gbtr_bg_com = GBTRegressor(maxIter=10, maxDepth=10,featuresCol='combine_features_bigram',labelCol='points',seed=42)
gbtr_bg_com_model = gbtr_bg_com.fit(rtrainingData_bigram)
gbtr_bg_com_predictions = gbtr_bg_com_model.transform(rtestData_bigram)


In [64]:
from pyspark.ml.evaluation import RegressionEvaluator
evaluator_r2 = RegressionEvaluator(predictionCol="prediction",labelCol='points',metricName="r2")
evaluator_mse = RegressionEvaluator(predictionCol="prediction",labelCol='points',metricName="mse")


print('gradient Boosting Evluation:')
print('using Tf-idf')
print('  using text only')
print('   R2: ' + str(evaluator_r2.evaluate(gbtr_tf_idf_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(gbtr_tf_idf_predictions)))

print('  using categorical features')
print('   R2: ' + str(evaluator_r2.evaluate(gbtr_num_cat_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(gbtr_num_cat_predictions)))

print('  combining Cat and Tfidf')
print('   R2: ' + str(evaluator_r2.evaluate(gbtr_com_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(gbtr_com_predictions)))

print('  selecting features')
print('   R2: ' + str(evaluator_r2.evaluate(gbtr_selected_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(gbtr_selected_predictions)))

print('using Word to Vec')
print('  using text only')
print('   R2: ' + str(evaluator_r2.evaluate(gbtr_w2v_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(gbtr_w2v_predictions)))
print('  using text & categorical')
print('   R2: ' + str(evaluator_r2.evaluate(gbtr_w2v_com_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(gbtr_w2v_com_predictions)))

print('using bigram')
print('  using text only')
print('   R2: ' + str(evaluator_r2.evaluate(gbtr_bg_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(gbtr_bg_predictions)))
print('  using text & categorical')
print('   R2: ' + str(evaluator_r2.evaluate(gbtr_bg_com_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(gbtr_bg_com_predictions)))

gradient Boosting Evluation:
using Tf-idf
 using text only
 R2: 0.35445947067175454
 MSE: 5.9660657593202995
 using categorical features
 R2: 0.446909970297931
 MSE: 5.111641079237471
 combining Cat and Tfidf
 R2: 0.5432673930132559
 MSE: 4.221108735874815
 selecting features
 R2: 0.5388880975032073
 MSE: 4.261582050570694
using Word to Vec
 using text only
 R2: 0.4692436950005663
 MSE: 4.905233480995523
 using text & categorical
 R2: 0.601238091544772
 MSE: 3.6853453192653896
using bigram
 using text only
 R2: 0.24212129120150871
 MSE: 7.004291766135465
 using text & categorical
 R2: 0.4913106715592517
 MSE: 4.7012911609130095

In [65]:
from pyspark.ml.regression import DecisionTreeRegressor

#TF-idf
DTR_tfidf= DecisionTreeRegressor(maxDepth=10,featuresCol='tf_idf_features',varianceCol="variance",labelCol='points')
DTR_tfidf_model= DTR_tfidf.fit(rtrainingData)
DTR_tfidf_predictions = DTR_tfidf_model.transform(rtestData)

DTR_num_cat= DecisionTreeRegressor(maxDepth=10,featuresCol='num_cat_features',varianceCol="variance",labelCol='points')
DTR_num_cat_model= DTR_num_cat.fit(rtrainingData)
DTR_num_cat_predictions = DTR_num_cat_model.transform(rtestData)

DTR_com= DecisionTreeRegressor(maxDepth=10,featuresCol='combine_features',varianceCol="variance",labelCol='points')
DTR_com_model= DTR_com.fit(rtrainingData)
DTR_com_predictions = DTR_com_model.transform(rtestData)

DTR_selected= DecisionTreeRegressor(maxDepth=10,featuresCol='selectedFeatures',varianceCol="variance",labelCol='points')
DTR_selected_model= DTR_selected.fit(rtrainingData)
DTR_selected_predictions = DTR_selected_model.transform(rtestData)

# For w2v model
DTR_w2v= DecisionTreeRegressor(maxDepth=10,featuresCol='word2vec_features',varianceCol="variance",labelCol='points')
DTR_w2v_model= DTR_w2v.fit(rtrainingData_w2v)
DTR_w2v_predictions = DTR_w2v_model.transform(rtestData_w2v)

DTR_w2v_com= DecisionTreeRegressor(maxDepth=10,featuresCol='combine_features_w2v',varianceCol="variance",labelCol='points')
DTR_w2v_com_model= DTR_w2v_com.fit(rtrainingData_w2v)
DTR_w2v_com_predictions = DTR_w2v_com_model.transform(rtestData_w2v)

# For bigram 
DTR_bg= DecisionTreeRegressor(maxDepth=10,featuresCol='bigram_features',varianceCol="variance",labelCol='points')
DTR_bg_model= DTR_bg.fit(rtrainingData_bigram)
DTR_bg_predictions = DTR_bg_model.transform(rtestData_bigram)

DTR_bg_com= DecisionTreeRegressor(maxDepth=10,featuresCol='combine_features_bigram',varianceCol="variance",labelCol='points')
DTR_bg_com_model= DTR_bg_com.fit(rtrainingData_bigram)
DTR_bg_com_predictions = DTR_bg_com_model.transform(rtestData_bigram)

In [66]:
from pyspark.ml.evaluation import RegressionEvaluator
evaluator_r2 = RegressionEvaluator(predictionCol="prediction",labelCol='points',metricName="r2")
evaluator_mse = RegressionEvaluator(predictionCol="prediction",labelCol='points',metricName="mse")


print('Decision Tree regressor:')
print('using Tf-idf')
print('  using text only')
print('   R2: ' + str(evaluator_r2.evaluate(DTR_tfidf_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(DTR_tfidf_predictions)))

print('  using categorical features')
print('   R2: ' + str(evaluator_r2.evaluate(DTR_num_cat_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(DTR_num_cat_predictions)))

print('  combining Cat and Tfidf')
print('   R2: ' + str(evaluator_r2.evaluate(DTR_com_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(DTR_com_predictions)))

print('  selecting features')
print('   R2: ' + str(evaluator_r2.evaluate(DTR_selected_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(DTR_selected_predictions)))

print('using Word to Vec')
print('  using text only')
print('   R2: ' + str(evaluator_r2.evaluate(DTR_w2v_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(DTR_w2v_predictions)))
print('  using text & categorical')
print('   R2: ' + str(evaluator_r2.evaluate(DTR_w2v_com_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(DTR_w2v_com_predictions)))

print('using bigram')
print('  using text only')
print('   R2: ' + str(evaluator_r2.evaluate(DTR_bg_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(DTR_bg_predictions)))
print('  using text & categorical')
print('   R2: ' + str(evaluator_r2.evaluate(DTR_bg_com_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(DTR_bg_com_predictions)))

Decision Tree regressor:
using Tf-idf
 using text only
 R2: 0.21850536483205096
 MSE: 7.222549432829244
 using categorical features
 R2: 0.4301062832578131
 MSE: 5.2669402391286475
 combining Cat and Tfidf
 R2: 0.4517658960856853
 MSE: 5.066762762143626
 selecting features
 R2: 0.45197307869898606
 MSE: 5.064847986790285
using Word to Vec
 using text only
 R2: 0.4014216122835573
 MSE: 5.532043087891622
 using text & categorical
 R2: 0.5346444331659277
 MSE: 4.300801866130592
using bigram
 using text only
 R2: 0.1873667040909851
 MSE: 7.510331979699979
 using text & categorical
 R2: 0.43852308916266647
 MSE: 5.18915237728201

In [67]:
from pyspark.ml.regression import LinearRegression

#TF-idf
lir_tfidf= LinearRegression(maxIter=5,featuresCol='tf_idf_features',labelCol='points')
lir_tfidf_model= lir_tfidf.fit(rtrainingData)
lir_tfidf_predictions = lir_tfidf_model.transform(rtestData)

lir_num_cat= LinearRegression(maxIter=5,featuresCol='num_cat_features',labelCol='points')
lir_num_cat_model= lir_num_cat.fit(rtrainingData)
lir_num_cat_predictions = lir_num_cat_model.transform(rtestData)

lir_com= LinearRegression(maxIter=5,featuresCol='combine_features',labelCol='points')
lir_com_model= lir_com.fit(rtrainingData)
lir_com_predictions = lir_com_model.transform(rtestData)

lir_selected= LinearRegression(maxIter=5,featuresCol='selectedFeatures',labelCol='points')
lir_selected_model= lir_selected.fit(rtrainingData)
lir_selected_predictions = lir_selected_model.transform(rtestData)

# For w2v model
lir_w2v= LinearRegression(maxIter=5,featuresCol='word2vec_features',labelCol='points')
lir_w2v_model= lir_w2v.fit(rtrainingData_w2v)
lir_w2v_predictions = lir_w2v_model.transform(rtestData_w2v)

lir_w2v_com= LinearRegression(maxIter=5,featuresCol='combine_features_w2v',labelCol='points')
lir_w2v_com_model= lir_w2v_com.fit(rtrainingData_w2v)
lir_w2v_com_predictions = lir_w2v_com_model.transform(rtestData_w2v)

# For bigram 
lir_bg= LinearRegression(maxIter=5,featuresCol='bigram_features',labelCol='points')
lir_bg_model= lir_bg.fit(rtrainingData_bigram)
lir_bg_predictions = lir_bg_model.transform(rtestData_bigram)

lir_bg_com= LinearRegression(maxIter=5,featuresCol='combine_features_bigram',labelCol='points')
lir_bg_com_model= lir_bg_com.fit(rtrainingData_bigram)
lir_bg_com_predictions = lir_bg_com_model.transform(rtestData_bigram)

In [68]:
evaluator_r2 = RegressionEvaluator(predictionCol="prediction",labelCol='points',metricName="r2")
evaluator_mse = RegressionEvaluator(predictionCol="prediction",labelCol='points',metricName="mse")


print('Linear regression:')
print('using Tf-idf')
print('  using text only')
print('   R2: ' + str(evaluator_r2.evaluate(lir_tfidf_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(lir_tfidf_predictions)))

print('  using categorical features')
print('   R2: ' + str(evaluator_r2.evaluate(lir_num_cat_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(lir_num_cat_predictions)))

print('  combining Cat and Tfidf')
print('   R2: ' + str(evaluator_r2.evaluate(lir_com_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(lir_com_predictions)))

print('  selecting features')
print('   R2: ' + str(evaluator_r2.evaluate(lir_selected_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(lir_selected_predictions)))

print('using Word to Vec')
print('  using text only')
print('   R2: ' + str(evaluator_r2.evaluate(lir_w2v_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(lir_w2v_predictions)))
print('  using text & categorical')
print('   R2: ' + str(evaluator_r2.evaluate(lir_w2v_com_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(lir_w2v_com_predictions)))

print('using bigram')
print('  using text only')
print('   R2: ' + str(evaluator_r2.evaluate(lir_bg_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(lir_bg_predictions)))
print('  using text & categorical')
print('   R2: ' + str(evaluator_r2.evaluate(lir_bg_com_predictions)))
print('   MSE: ' + str(evaluator_mse.evaluate(lir_bg_com_predictions)))

Linear regression:
using Tf-idf
 using text only
 R2: 0.6460008719370833
 MSE: 3.2716490767251347
 using categorical features
 R2: 0.26743731379773006
 MSE: 6.770321862292764
 combining Cat and Tfidf
 R2: 0.6878619954998357
 MSE: 2.8847698575469036
 selecting features
 R2: 0.6787428599809173
 MSE: 2.969048628131045
using Word to Vec
 using text only
 R2: 0.5680501646782388
 MSE: 3.992067120772248
 using text & categorical
 R2: 0.5728208676109804
 MSE: 3.9479764306887963
using bigram
 using text only
 R2: 0.26525496934125425
 MSE: 6.790491022779669
 using text & categorical
 R2: 0.25907642647467943
 MSE: 6.847592926322616

## 5. Cross Validation & Hyper-Parameters Tuning

In [70]:
lr_selected=lr_selected = LogisticRegression(featuresCol='selectedFeatures')
pipeline = Pipeline(stages=[regexTokenizer, stopwordsRemover, hashingTF, idf, bucketizer_3, bucketizer_6]+ indexers+ [encoder, assembler_num_cat, assembler_combine, chi_selector, lr_selected])
paramGrid = ParamGridBuilder() \
    .addGrid(hashingTF.numFeatures, [2000, 5000]) \
    .addGrid(lr_selected.regParam, [ 0.1, 0.01]) \
    .addGrid(chi_selector.numTopFeatures, [500, 1000]) \
    .build()

In [71]:
lr_combine_w2v = LogisticRegression(featuresCol='combine_features_w2v')
pipeline_w2v = Pipeline(stages=[regexTokenizer, stopwordsRemover, word2vec, bucketizer_3, bucketizer_6]+ indexers+ [encoder, assembler_num_cat, assembler_combine_w2v,lr_combine_w2v])
paramGrid_w2v = ParamGridBuilder() \
    .addGrid(word2vec.vectorSize, [ 300, 500]) \
    .addGrid(word2vec.minCount, [ 5, 7]) \
    .addGrid(lr_combine_w2v.regParam, [ 0.1, 0.01]) \
    .build()

In [72]:
crossval = CrossValidator(estimator=pipeline,
                          estimatorParamMaps=paramGrid,
                          evaluator=evaluator_f1,
                          numFolds=5,
                          parallelism=5)

In [73]:
crossval_w2v = CrossValidator(estimator=pipeline_w2v,
                          estimatorParamMaps=paramGrid_w2v,
                          evaluator=evaluator_f1,
                          numFolds=5,
                          parallelism=5)

In [74]:
(trainingData_df_lower, testData_df_lower) = df_lower.randomSplit([0.8, 0.2], seed = 100)
print("Training Dataset Count: " + str(trainingData.count()))
print("Test Dataset Count: " + str(testData.count()))

Training Dataset Count: 96685
Test Dataset Count: 24231

In [75]:
cvModel = crossval.fit(trainingData_df_lower)

In [76]:
cvModel_w2v = crossval_w2v.fit(trainingData_df_lower)

In [77]:
prediction_cv = cvModel.transform(testData_df_lower)

In [78]:
prediction_cv_w2v= cvModel_w2v.transform(testData_df_lower)

In [79]:
print('CV Evaluation')
print('f1: ' + str(evaluator_f1.evaluate(prediction_cv)))
print('acc: ' + str(evaluator_acc.evaluate(prediction_cv)))
print('recall: ' + str(evaluator_recall.evaluate(prediction_cv)))
print('precision: ' + str(evaluator_precision.evaluate(prediction_cv)))

CV Evaluation
f1: 0.8215280669100056
acc: 0.8293508315793818
recall: 0.8293508315793817
precision: 0.8241890702519536

In [80]:
print('CV Evaluation for word2vec')
print('f1: ' + str(evaluator_f1.evaluate(prediction_cv_w2v)))
print('acc: ' + str(evaluator_acc.evaluate(prediction_cv_w2v)))
print('recall: ' + str(evaluator_recall.evaluate(prediction_cv_w2v)))
print('precision: ' + str(evaluator_precision.evaluate(prediction_cv_w2v)))

CV Evaluation for word2vec
f1: 0.800366650092285
acc: 0.8135859023564855
recall: 0.8135859023564854
precision: 0.8065784720689302

In [81]:
bestPipeline = cvModel.bestModel
best_NumFeatures = best_model._java_obj.getNumFeatures()
best_RegParam= best_model._java_obj.getRegParam()
best_numTopFeatures= best_model._java_obj.getNumTopFeatures()

In [82]:
# cross validation on TFIDF with categorical feature combined on linear regression initial r2 = 0.68
rpipeline = Pipeline(stages=[regexTokenizer, stopwordsRemover, hashingTF, idf, bucketizer_3, bucketizer_6]+ indexers+ [encoder, assembler_num_cat, assembler_combine, chi_selector, lir_com])

rparamGrid =ParamGridBuilder() \
    .addGrid(hashingTF.numFeatures, [5000]) \
    .addGrid(lir_com.maxIter, [10]) \
    .addGrid(chi_selector.numTopFeatures, [2000]) \
    .build()

rcrossval = CrossValidator(estimator=rpipeline,
                          estimatorParamMaps=rparamGrid,
                          evaluator=evaluator_r2,
                          numFolds=5,
                          parallelism=5)

rcvModel = rcrossval.fit(trainingData_df_lower)
rprediction_cv = rcvModel.transform(testData_df_lower)
rbestPipeline = rcvModel.bestModel

print('R2 for CV is',evaluator_r2.evaluate(rprediction_cv))

R2 for CV is 0.693768225980921

In [83]:
# cross validation on word 2 vec with categorical feature combined on DTR initial r2 = 0.531
rpipeline_w2v = Pipeline(stages=[regexTokenizer, stopwordsRemover, word2vec, bucketizer_3, bucketizer_6]+ indexers+ [encoder, assembler_num_cat, assembler_combine_w2v,DTR_w2v_com])
rparamGrid_w2v = ParamGridBuilder() \
    .addGrid(word2vec.vectorSize, [300]) \
    .addGrid(word2vec.minCount, [5]) \
    .addGrid(DTR_w2v_com.maxDepth, [10]) \
    .build()

crossval_w2v = CrossValidator(estimator=rpipeline_w2v,
                          estimatorParamMaps=rparamGrid_w2v,
                          evaluator=evaluator_r2,
                          numFolds=5,
                          parallelism=5)

rcv_w2v_Model = crossval_w2v.fit(trainingData_df_lower)
rprediction_cv_w2v = rcv_w2v_Model.transform(testData_df_lower)
rbestPipeline_w2v = rcv_w2v_Model.bestModel

print('R2 for CV is',evaluator_r2.evaluate(rprediction_cv_w2v))

R2 for CV is 0.5330813180852416

In [84]:
display(rprediction_cv.select('points','prediction'))

points prediction 87 87.56638736363274 87 87.49541822729047 87 88.02602216197685 87 88.68874086441022 87 85.81119432763244 87 87.66704539727766 87 85.14620909559216 87 85.8648762698289 87 87.09415365092077 86 83.63839148910621 86 85.58912126602948 86 85.66790650113177 85 86.25298115113219 86 85.17255382630444 86 88.28030968089192 86 86.93368063649173 86 84.96977746993723 86 87.98400773160976 88 86.85588833285256 88 89.8338958077846 88 85.15256676080395 88 87.45239021375559 87 90.35292525393838 92 93.5779370336114 92 89.73167227986116 92 89.24537164975281 91 91.72547348125084 91 94.22947373854412 91 92.95005226072719 91 91.64512220404355 91 91.01398341875725 88 91.33063249025477 88 86.8677788613323 87 87.97034655823583 87 87.03906266826058 90 87.37349247938737 90 91.85992186557505 90 88.66891072850375 90 89.9877586761789 90 90.49491119899639 90 88.25442599111423 90 87.80201789029329 85 85.64776670757325 85 87.94712721816632 85 87.54248102418303 85 84.28193971988698 85 87.17179069142455 85 85.70567762185173 85 84.96520134785942 85 83.59997940313971 89 86.71887000205709 89 87.9166881864908 89 87.2835913088875 89 86.9155613093063 89 88.07088152649094 89 88.6007085897201 89 87.44936475587721 89 87.16749023517839 92 93.85960988313275 87 87.28923446571558 87 88.45556390541773 87 88.20213885052091 86 87.06272881813251 86 85.62068439750283 96 93.70080988159667 95 92.407644989607 88 87.75634970170854 88 87.57407109326788 88 88.87140694416661 88 87.66263372688562 85 86.64198704380195 85 85.03584969390012 85 86.29821813932037 89 86.8694051154637 89 88.30263963951283 89 89.62353925594122 89 88.34869765027271 89 89.28015774726454 89 91.69713240304273 89 89.02026125048816 89 89.09092347795719 89 89.22822517180981 92 90.45250141343068 92 89.24215436005503 92 90.7813809163192 92 91.78637093094231 92 91.2388282197639 87 88.05989129873588 87 86.21867301058275 87 87.99680507829676 87 87.80889705668157 87 85.49706720808294 87 86.72773436153834 87 86.47107862146616 87 85.87554183693983 91 90.53505126193204 91 90.69751399997966 91 91.5744543577069 91 91.50340947446246 91 94.37706503486459 93 92.6839266605098 93 90.94777571900227 93 91.74167953462555 93 92.0922324491144 89 88.46897812277125 89 90.25505047771226 89 89.60664008845826 89 88.30033631467386 87 87.74544080579251 87 85.197756521336 87 85.97896655272633 87 84.65945986584391 87 86.54082271342493 92 91.16877935463383 92 90.27121624501832 92 92.54729754804156 92 89.44323858983726 92 88.59237701835052 92 90.72971864482066 92 89.90761110331194 92 90.14846186907795 92 90.59159302453105 92 89.58122864670061 90 89.69628989016516 90 88.06527998746851 90 87.87914170575925 90 88.56678858515103 90 89.86409524769296 90 91.08029645397272 90 91.71815814959473 90 88.0443604254704 90 89.7632365242477 90 87.69596084451653 91 90.54441606634487 91 91.45332048328721 91 89.07619151970366 91 91.60854470201161 91 90.49325714723749 85 85.91399304248701 85 86.26768053346858 85 85.27941003034427 85 84.83382452613603 85 83.4705969952953 85 85.76278467804524 87 88.87729515379668 87 87.27994168243939 87 86.51098513357734 87 87.78307107424862 92 89.52341023622004 90 87.74889428334467 90 88.19041999231005 90 90.67546110630765 90 88.63668771066234 90 88.40983301815602 90 89.05449019579318 90 90.58833016517264 90 88.43638616562696 90 88.36662731378172 90 88.73541828216518 90 88.63609030667338 90 88.53233848512573 90 88.10467322964483 86 87.73048714875868 86 89.6827703271328 86 87.41215010249056 86 85.68155406180796 86 85.59885799691614 90 90.13582579246692 90 90.38476161436166 90 89.63402459865866 90 88.72010906599358 90 89.49531027091398 90 90.16541502837073 90 90.12353888553095 90 91.36761259422747 90 91.60138425919473 87 87.94478304182239 87 85.10354925271007 87 87.42281274668969 87 87.31369590174009 87 87.78517457515167 87 87.87152753412434 87 88.91370196707811 87 87.3157072989664 87 89.04262055775543 87 86.4281765386062 87 87.99600831458132 85 87.11238472909484 85 86.05163753900564 85 86.14006096609971 85 83.34244148737